# Symbolic regression

In [ ]:
objective = """
function my_custom_objective(tree, dataset::Dataset{T,L}, options) where {T,L} 
    penalty_term = L(0)
    tot_features = 1:7
    tol = L(0.0000000000000001)
    
    P_pred = dataset.X[1,:]
    
    if tree.degree != 2
        penalty_term += L(10000)
    else
        fn = tree.l
        features=[1,2] #function of only fck or delta
        remain_feat = setdiff(tot_features, features)
        should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
        should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
        penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
        vfc, flag = eval_tree_array(fn, dataset.X, options)
        if !flag
            return L(Inf)
        end
        penalty_term += any(x -> x < 0, vfc) ? L(100) : L(0)
            
        if  tree.r.degree != 2  
            penalty_term += L(10000)
        else
            fn = tree.r.r
            features=[1,3,6] #function of only fck or delta
            remain_feat = setdiff(tot_features, features)
            should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
            should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
            penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
            vs, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vs) ? L(100) : L(0)

            fn = tree.r.l
            features=[1,4,5,7] #function of only fck or delta
            remain_feat = setdiff(tot_features, features)
            should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
            should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
            penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
            vf, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vf) ? L(100) : L(0)
            P_pred = (vfc .+  vs .+  vf) 
        end
    end
    dims = size(dataset.y)
    #println("y: ", dims)
    dims = size(P_pred)
    #println("P_pred: ", dims)
    r = dataset.y ./P_pred .- 1.0
    MAPE = sum(abs.(r)) ./ length(r)
    return ( penalty_term  + MAPE )
end

my_custom_objective
"""
from pysr import PySRRegressor
import numpy as np
import scipy.io as sio
import pandas as pd
data = pd.read_excel('data111.xlsx', sheet_name='1_17')
PC = data[data['ff'] != 0][['fc', 'he', 'hf', 'bw', 'bf', 'Ls/he', 'fst Ast', 'Sst/he', 'Al', 'ff', 'EfAf', 'Sf/he', 'Rg', 'alfa_f', 'V']].copy();PC['Vexp']=PC['V']
PC['alfa_f'] = PC['alfa_f'] * (np.pi / 180)
PC['si_co']=np.sin(PC['alfa_f'])+np.cos(PC['alfa_f'])
PC['fr']=PC['EfAf']/PC['bw']/PC['he']
PC['fs']=PC['fst Ast']/PC['bw']/PC['he']

X = PC[['fc', 'Ls/he', 'fs', 'Sst/he', 'Sf/he','fr', 'si_co']];     PC['vs'] = PC['V']/PC['bw']/PC['he']


PC['L_d']=PC['Ls/he'];PC['sst']=PC['Sst/he'];PC['sf']=PC['Sf/he'];PC['fs']=np.maximum(0.001,PC['fs']);PC['fr']=np.maximum(0.001,PC['fr'])

features = ['fc','L_d', 'sst', 'sf', 'si_co', 'fs','fr']
X=PC[features];y=PC['vs']

modelior11=[]
for j in range(100):
    #population_size is the equation size
    model7 = PySRRegressor(niterations=20,populations=40,population_size=35,maxsize=35,
                      nested_constraints={"^":{"^":1}},parsimony= 0.01,#adaptive_parsimony_scaling=1000,
                      constraints={"^":(-1,10)},
                      binary_operators=["+", "*","^"],#elementwise_loss="f(x, y) = ((x+0.00001)/(y+0.00001)-1.0)^2"#special(x,y)=x^2.0+y
                      loss_function=objective,model_selection ='accuracy',
                      )
    model7.fit(X,y)
    i=0
    modelior11.append(model7)
    while i <len(model7.equations_):
        print(model7.sympy(i))
        i=i+1

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.400e+05
Head worker occupation: 17.9%
Progress: 329 / 800 total iterations (41.125%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fc
5           6.010e+02  7.030e-01  y = (L_d ^ (sf + fs))
7           5.010e+02  9.099e-02  y = (L_d * ((sf ^ fr) ^ fs))
9           4.010e+02  1.113e-01  y = (L_d + ((sf ^ fr) * (sst * fs)))
11          3.010e+02  1.434e-01  y = (L_d ^ ((fc * (sf ^ fr)) * (sst * fs)))
13          2.010e+02  2.019e-01  y = (L_d + ((sf ^ (fr ^ si_co)) * (sst * (fs ^ fc))))
15          1.010e+02  3.441e-01  y = ((L_d + fc) * ((si_co ^ (sf + fc)) + ((fc + sst) ^ fs)))
17          1.000e+00  2.308e+00  y = ((L_d + fc) + (((si_co + fr) + (sf + fc)) ^ ((fc * fs) * s...
                                  st)))
21          9.918e-01  2.063e-03  y = (((fc * L_d) ^ -0.20729) + ((((fc + fr) * (si_co * s

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.400e+05
Head worker occupation: 13.1%
Progress: 332 / 800 total iterations (41.500%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.2501
5           6.010e+02  7.030e-01  y = (L_d ^ (sf + fs))
7           5.010e+02  9.099e-02  y = (L_d + ((sf ^ fr) * fs))
9           4.010e+02  1.113e-01  y = (L_d * ((sf ^ fc) * (fs * sst)))
11          3.010e+02  1.434e-01  y = (L_d ^ ((sf ^ fc) * ((fs ^ fc) * sst)))
13          2.010e+02  2.019e-01  y = (L_d + ((sf ^ (fc * si_co)) + (fc ^ (fs * sst))))
15          1.010e+02  3.441e-01  y = (L_d * ((((fc + fr) * sf) + si_co) ^ (fc ^ (sst * fs))))
17          1.010e+02  5.782e-06  y = (L_d * (((((fc + sf) + fr) ^ -1.0851) * si_co) * (sst ^ (f...
                                  s * fc))))
19          9.889e-01  2.313e+00  y = (((L_d ^ fc) ^ -0.46135) * (((si_co + fr) *

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!


...


Expressions evaluated per second: 1.350e+05
Head worker occupation: 15.9%
Progress: 307 / 800 total iterations (38.375%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.38727
5           6.010e+02  7.030e-01  y = (L_d * (sf * fs))
7           5.010e+02  9.099e-02  y = (L_d + ((sf ^ fr) * fs))
9           4.010e+02  1.113e-01  y = (L_d * ((sf ^ fr) ^ (fs ^ fc)))
11          3.010e+02  1.434e-01  y = (L_d * (((sf ^ fr) * si_co) ^ (fs ^ fc)))
13          2.010e+02  2.019e-01  y = (L_d + ((sf ^ (fc * si_co)) + (fs ^ (sst + fc))))
15          1.010e+02  3.441e-01  y = (fc * (((si_co * fc) + (fr ^ sf)) * ((sst + fc) ^ fs)))
17          1.010e+02  2.533e-06  y = (L_d + (((sf * fr) ^ (si_co * (fc * -0.36152))) ^ ((sst * ...
                                  fs) * fc)))
19          1.000e+00  2.308e+00  y = ((fc * L_d) * (((fr * ((sf * fc) + fr)) +

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.280e+05
Head worker occupation: 17.6%
Progress: 297 / 800 total iterations (37.125%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = sf
5           6.010e+02  7.030e-01  y = (L_d * (sf * fs))
7           5.010e+02  9.099e-02  y = (L_d * ((sf ^ fc) + fs))
9           4.010e+02  1.113e-01  y = (L_d + ((sf ^ fr) * (fs * sst)))
11          3.010e+02  1.434e-01  y = (L_d ^ ((sf ^ (si_co * (fc + fr))) + fs))
13          2.010e+02  2.019e-01  y = (L_d + (((sf ^ fc) + si_co) ^ ((fs + sst) ^ fc)))
15          1.010e+02  3.441e-01  y = (fc + ((((fc + fr) ^ sf) ^ si_co) + (fc * (sst * fs))))
17          1.000e+00  2.308e+00  y = ((fc + L_d) + ((((si_co ^ fr) * fc) + sf) + ((fc + sst) + ...
                                  fs)))
19          1.000e+00  1.004e-05  y = ((L_d * fc) * (((si_co * sf) ^ ((1.6239 + fr) + fc)

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.380e+05
Head worker occupation: 14.2%
Progress: 322 / 800 total iterations (40.250%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.2501
5           6.010e+02  7.030e-01  y = (L_d ^ (sf + fs))
7           5.010e+02  9.099e-02  y = (L_d * ((sf ^ fc) ^ fs))
9           4.010e+02  1.113e-01  y = (L_d * ((sf ^ fr) ^ (sst * fs)))
11          3.010e+02  1.434e-01  y = (L_d * (((sf ^ fr) * fc) ^ (sst * fs)))
13          2.010e+02  2.019e-01  y = (L_d * (((sf ^ fr) * si_co) + (fs ^ (sst * fc))))
15          1.010e+02  3.441e-01  y = ((fc + L_d) + (((si_co + fc) + sf) + ((fc * sst) * fs)))
17          1.000e+00  2.308e+00  y = ((L_d + fc) * ((((sf + fc) + si_co) + fr) + ((fc + sst) ^ ...
                                  fs)))
23          9.989e-01  1.754e-04  y = (((L_d ^ -1.19) ^ fc) + ((((si_co * fr) ^ -0.851

In [1]:
objective = """
function my_custom_objective(tree, dataset::Dataset{T,L}, options) where {T,L} 
    penalty_term = L(0)
    tot_features = 1:7
    tol = L(0.0000000000000001)
    
    P_pred = dataset.X[1,:]
    
    if tree.degree != 2
        penalty_term += L(10000)
    else
        fn = tree.l
        features=[1,2] #function of only fck or delta
        remain_feat = setdiff(tot_features, features)
        should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
        should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
        penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
        vfc, flag = eval_tree_array(fn, dataset.X, options)
        if !flag
            return L(Inf)
        end
        penalty_term += any(x -> x < 0, vfc) ? L(100) : L(0)
            
        if  tree.r.degree != 2  
            penalty_term += L(10000)
        else
            fn = tree.r.r
            vs, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vs) ? L(100) : L(0)

            fn = tree.r.l
            vf, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vf) ? L(100) : L(0)
            P_pred = (vfc .+  vs .+  vf) 
        end
    end
    dims = size(dataset.y)
    #println("y: ", dims)
    dims = size(P_pred)
    #println("P_pred: ", dims)
    r = dataset.y ./P_pred .- 1.0
    MAPE = sum(abs.(r)) ./ length(r)
    return ( penalty_term  + MAPE )
end

my_custom_objective
"""
from pysr import PySRRegressor
import numpy as np
import scipy.io as sio
import pandas as pd
#aaaaaaaaaaaa
data = pd.read_excel('data111.xlsx', sheet_name='1_17')
PC = data[data['ff'] != 0][['fc', 'he', 'hf', 'bw', 'bf', 'Ls/he', 'fst Ast', 'Sst/he', 'Al', 'ff', 'EfAf', 'Sf/he', 'Rg', 'alfa_f', 'V']].copy();PC['Vexp']=PC['V']
PC['alfa_f'] = PC['alfa_f'] * (np.pi / 180)
PC['si_co']=np.sin(PC['alfa_f'])+np.cos(PC['alfa_f'])
PC['fr']=PC['EfAf']/PC['bw']/PC['he']
PC['fs']=PC['fst Ast']/PC['bw']/PC['he']

X = PC[['fc', 'Ls/he', 'fs', 'Sst/he', 'Sf/he','fr', 'si_co']];     PC['vs'] = PC['V']/PC['bw']/PC['he']


PC['L_d']=PC['Ls/he'];PC['sst']=PC['Sst/he'];PC['sf']=PC['Sf/he'];PC['fs']=np.maximum(0.001,PC['fs']);PC['fr']=np.maximum(0.001,PC['fr'])

features = ['fc','L_d', 'sst', 'sf', 'si_co', 'fs','fr']
X=PC[features];y=PC['vs']

modelior11=[]
for j in range(2):
    #population_size is the equation size
    model7 = PySRRegressor(niterations=100,populations=40,population_size=35,maxsize=35,
                      nested_constraints={"^":{"^":1}},parsimony= 0.01,#adaptive_parsimony_scaling=1000,
                      constraints={"^":(-1,10)},
                      binary_operators=["+", "*","^"],#elementwise_loss="f(x, y) = ((x+0.00001)/(y+0.00001)-1.0)^2"#special(x,y)=x^2.0+y
                      loss_function=objective,model_selection ='accuracy',
                      )
    model7.fit(X,y)
    i=0
    modelior11.append(model7)
    while i <len(model7.equations_):
        print(model7.sympy(i))
        i=i+1

Detected Jupyter notebook. Loading juliacall extension. Set `PYSR_AUTOLOAD_EXTENSIONS=no` to disable.


c:\Users\osama\anaconda3\lib\site-packages\pandas\core\computation\expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.8.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
c:\Users\osama\anaconda3\lib\site-packages\pandas\core\arrays\masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.4' currently installed).
  from pandas.core import (
c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(


Compiling Julia backend...


[ Info: Started!



Expressions evaluated per second: 1.540e+05
Head worker occupation: 13.2%
Progress: 350 / 4000 total iterations (8.750%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = L_d
5           1.010e+02  1.149e+00  y = (L_d ^ (0.0011672 + 0.0011672))
7           9.999e-01  2.308e+00  y = ((fc + L_d) * (si_co + sf))
9           5.515e-01  2.975e-01  y = (((0.01855 ^ fc) * L_d) * (0.00402 * 0.00402))
11          2.742e-01  3.494e-01  y = (((0.72761 ^ fc) * L_d) * ((0.72761 ^ fc) * 0.00402))
13          2.052e-01  1.450e-01  y = (((0.01855 ^ fc) * L_d) * (((0.056663 ^ fc) ^ fr) * 0.0040...
                                  2))
27          2.019e-01  1.156e-03  y = ((((-1.4759 + (0.15711 + -0.14986)) + (3.4417 + (L_d * fc)...
                                  )) ^ -2.8962) * (((fc ^ (0.75152 + L_d)) ^ (-0.4505 * L_d)) * ...
                             

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.640e+05
Head worker occupation: 12.7%
Progress: 361 / 4000 total iterations (9.025%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = -0.47577
5           1.010e+02  1.149e+00  y = (L_d + (0.0041316 + 0.0041316))
7           9.999e-01  2.308e+00  y = ((fc + L_d) + (si_co + 0.50931))
9           3.880e-01  4.733e-01  y = (((L_d ^ -1.0872) ^ fc) * (0.0029454 ^ 0.0029454))
11          2.067e-01  3.150e-01  y = (((L_d ^ -2.1281) ^ fc) + (0.0029454 * (0.0041316 * fs)))
19          2.036e-01  1.840e-03  y = (((L_d ^ (-1.3367 + fc)) ^ -1.0181) + ((0.0024244 + (0.002...
                                  4244 ^ fc)) + (0.0024244 * (0.056672 + 0.54152))))
21          2.026e-01  2.441e-03  y = ((((fc + L_d) * ((fc + L_d) ^ L_d)) ^ -1.44) * ((0.37542 ^...
                                   ((fc + -1.2478) + fc)) ^ 0.00

In [1]:
#PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
#binary_operators=["*","^"]
#features=[1,3,6]
#nested_constraints={"^":{"^":0}}
#parsimony= 0.00
objective = """
function my_custom_objective(tree, dataset::Dataset{T,L}, options) where {T,L} 
    penalty_term = L(0)
    tot_features = 1:7
    tol = L(0.0000000000000001)
    
    P_pred = dataset.X[1,:]
    
    if tree.degree != 2
        penalty_term += L(10000)
    else
        fn = tree.l
        features=[1,2] #function of only fck or delta
        remain_feat = setdiff(tot_features, features)
        should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
        should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
        penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
        vfc, flag = eval_tree_array(fn, dataset.X, options)
        if !flag
            return L(Inf)
        end
        penalty_term += any(x -> x < 0, vfc) ? L(100) : L(0)
            
        if  tree.r.degree != 2  
            penalty_term += L(10000)
        else
            fn = tree.r.r
            features=[1,3,6] #function of only fck or delta
            remain_feat = setdiff(tot_features, features)
            should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
            should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
            penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
            vs, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vs) ? L(100) : L(0)

            fn = tree.r.l
            features=[1,4,5,7] #function of only fck or delta
            remain_feat = setdiff(tot_features, features)
            should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
            should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
            penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
            vf, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vf) ? L(100) : L(0)
            P_pred = (vfc .+  vs .+  vf) 
        end
    end
    dims = size(dataset.y)
    #println("y: ", dims)
    dims = size(P_pred)
    #println("P_pred: ", dims)
    r = dataset.y ./P_pred .- 1.0
    MAPE = sum(abs.(r)) ./ length(r)
    return ( penalty_term  + MAPE )
end

my_custom_objective
"""
from pysr import PySRRegressor
import numpy as np
import scipy.io as sio
import pandas as pd
#aaaaaaaaaaaa
data = pd.read_excel('data111.xlsx', sheet_name='1_17')
PC = data[data['ff'] != 0][['fc', 'he', 'hf', 'bw', 'bf', 'Ls/he', 'fst Ast', 'Sst/he', 'Al', 'ff', 'EfAf', 'Sf/he', 'Rg', 'alfa_f', 'V']].copy();PC['Vexp']=PC['V']
PC['alfa_f'] = PC['alfa_f'] * (np.pi / 180)
PC['si_co']=np.sin(PC['alfa_f'])+np.cos(PC['alfa_f'])
PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
PC['fs']=PC['fst Ast']/PC['bw']/PC['he']

X = PC[['fc', 'Ls/he', 'fs', 'Sst/he', 'Sf/he','fr', 'si_co']];     PC['vs'] = PC['V']/PC['bw']/PC['he']*1000.0


PC['L_d']=PC['Ls/he'];PC['sst']=PC['Sst/he'];PC['sf']=PC['Sf/he'];PC['fs']=np.maximum(0.001,PC['fs']);PC['fr']=np.maximum(0.001,PC['fr'])

features = ['fc','L_d', 'sst', 'sf', 'si_co', 'fs','fr']
X=PC[features];y=PC['vs']

modelior11=[]
for j in range(20):
    #population_size is the equation size
    model7 = PySRRegressor(niterations=100,populations=40,population_size=35,maxsize=35,
                      nested_constraints={"^":{"^":0}},parsimony= 0.00,#adaptive_parsimony_scaling=1000,
                      constraints={"^":(-1,10)},
                      binary_operators=["*","^"],#elementwise_loss="f(y, x) = ((x+0.00001)/(y+0.00001)-1.0)^2",#special(x,y)=x^2.0+y
                      model_selection ='accuracy',loss_function=objective,should_simplify=False,use_frequency=False
                      )
    model7.fit(X,y)
    i=0
    modelior11.append(model7)
    while i <len(model7.equations_):
        print(model7.sympy(i))
        i=i+1

Detected Jupyter notebook. Loading juliacall extension. Set `PYSR_AUTOLOAD_EXTENSIONS=no` to disable.


c:\Users\osama\anaconda3\lib\site-packages\pandas\core\computation\expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.8.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
c:\Users\osama\anaconda3\lib\site-packages\pandas\core\arrays\masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.4' currently installed).
  from pandas.core import (
c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(


Compiling Julia backend...


[ Info: Started!



Expressions evaluated per second: 8.420e+04
Head worker occupation: 9.1%
Progress: 160 / 4000 total iterations (4.000%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 1.4146
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.110e-02  y = (L_d * ((si_co * sf) ^ sst))
9           4.003e+02  1.114e-01  y = (L_d * (((si_co * sf) * fr) ^ sst))
11          3.003e+02  1.437e-01  y = (L_d * (((si_co * sf) * fr) * (fs ^ sst)))
13          2.006e+02  2.017e-01  y = (L_d * (((si_co * sf) * fr) * ((sst * fc) * fs)))
15          1.006e+02  3.452e-01  y = (L_d * ((((fr * sf) ^ fc) * si_co) * ((sst * fc) ^ fs)))
17          9.638e-01  2.324e+00  y = ((L_d * fc) * ((fr * ((si_co * sf) ^ fc)) * ((fs * fc) ^ s...
                                  st)))
19          3.451e-01  5.135e-01  y = (((fc ^ -0.18171) * L_d) * (((fr ^ s

...


Expressions evaluated per second: 9.320e+04
Head worker occupation: 12.7%
Progress: 189 / 4000 total iterations (4.725%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fc
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.108e-02  y = (L_d ^ ((si_co * sf) * fs))
9           4.003e+02  1.115e-01  y = (L_d * ((si_co * fr) * (fs ^ fc)))
11          3.009e+02  1.428e-01  y = (L_d ^ (((si_co * (sf * fc)) * fr) * fs))
13          2.009e+02  2.019e-01  y = (fc * (((fc ^ si_co) * sf) * ((fs * sst) ^ fc)))
15          1.007e+02  3.453e-01  y = (L_d * (((si_co * (fr * fc)) ^ sf) * (fs * (sst ^ fc))))
17          9.619e-01  2.326e+00  y = ((fc * L_d) * ((fr * ((sf * si_co) ^ fc)) * ((fs * sst) ^ ...
                                  fc)))
19          3.809e-01  4.631e-01  y = (((fc ^ 0.12962) * L_d) * (((si_co * sf) ^ 

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 8.730e+04
Head worker occupation: 10.0%
Progress: 168 / 4000 total iterations (4.200%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fc
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.110e-02  y = (L_d * ((si_co * sf) ^ sst))
9           4.008e+02  1.108e-01  y = (L_d * (((si_co * fc) * sf) ^ sst))
11          3.008e+02  1.435e-01  y = (L_d * (((si_co * fc) * sf) ^ (sst * fs)))
13          2.009e+02  2.020e-01  y = (L_d * (((si_co * fc) * sf) ^ ((sst * fc) * fs)))
15          1.006e+02  3.456e-01  y = (L_d * ((((si_co * sf) ^ fc) * fr) * (sst * (fs ^ fc))))
17          9.605e-01  2.326e+00  y = ((L_d * fc) * (((sf ^ (si_co * fc)) * fr) * ((fc * sst) ^ ...
                                  fs)))
19          2.859e-01  6.059e-01  y = (((L_d * fc) ^ 0.15461) * (((sf ^ (si_c

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 8.590e+04
Head worker occupation: 10.1%
Progress: 170 / 4000 total iterations (4.250%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fc
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.110e-02  y = (L_d * ((si_co * sf) ^ sst))
9           4.007e+02  1.110e-01  y = (L_d * ((sf * si_co) ^ (fs * fc)))
11          3.004e+02  1.440e-01  y = (L_d * ((sf ^ fr) * ((sst * fs) ^ fc)))
13          2.010e+02  2.010e-01  y = ((fc * L_d) * ((sf ^ si_co) * ((sst * fs) ^ fc)))
15          1.007e+02  3.454e-01  y = (L_d * (((si_co * fc) * (sf ^ fr)) * ((sst * fs) ^ fc)))
17          9.615e-01  2.326e+00  y = ((L_d * fc) * ((((sf ^ fc) * fr) * si_co) * ((fc * fs) ^ s...
                                  st)))
19          3.746e-01  4.713e-01  y = (((L_d * fc) ^ 0.24708) * (((sf ^ fc) * (si

In [ ]:
#PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
#binary_operators=["*","^"]
#features=[1,3,6]
#nested_constraints={"^":{"^":0}}
#parsimony= 0.00
objective = """
function my_custom_objective(tree, dataset::Dataset{T,L}, options) where {T,L} 
    penalty_term = L(0)
    tot_features = 1:7
    tol = L(0.0000000000000001)
    
    P_pred = dataset.X[1,:]
    
    if tree.degree != 2
        penalty_term += L(10000)
    else
        fn = tree.l
        features=[1,2] #function of only fck or delta
        remain_feat = setdiff(tot_features, features)
        should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
        should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
        penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
        vfc, flag = eval_tree_array(fn, dataset.X, options)
        if !flag
            return L(Inf)
        end
        penalty_term += any(x -> x < 0, vfc) ? L(100) : L(0)
            
        if  tree.r.degree != 2  
            penalty_term += L(10000)
        else
            fn = tree.r.r
            features=[1,3,6] #function of only fck or delta
            remain_feat = setdiff(tot_features, features)
            should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
            should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
            penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
            vs, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vs) ? L(100) : L(0)

            fn = tree.r.l
            features=[1,4,5,7] #function of only fck or delta
            remain_feat = setdiff(tot_features, features)
            should_nt = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in remain_feat]
            should = [any(n -> n.degree == 0 && n.constant == false && n.feature == f, fn) for f in features]
            penalty_term += L(100) * (sum(should_nt)) + L(100) * (length(features) - sum(should))
            vf, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vf) ? L(100) : L(0)
            P_pred = (vfc .+  vs .+  vf) 
        end
    end
    dims = size(dataset.y)
    #println("y: ", dims)
    dims = size(P_pred)
    #println("P_pred: ", dims)
    r = dataset.y ./P_pred .- 1.0
    MAPE = sum(abs.(r)) ./ length(r)
    return ( penalty_term  + MAPE )
end

my_custom_objective
"""
from pysr import PySRRegressor
import numpy as np
import scipy.io as sio
import pandas as pd
#aaaaaaaaaaaa
data = pd.read_excel('data111.xlsx', sheet_name='1_17')
PC = data[data['ff'] != 0][['fc', 'he', 'hf', 'bw', 'bf', 'Ls/he', 'fst Ast', 'Sst/he', 'Al', 'ff', 'EfAf', 'Sf/he', 'Rg', 'alfa_f', 'V']].copy();PC['Vexp']=PC['V']
PC['alfa_f'] = PC['alfa_f'] * (np.pi / 180)
PC['si_co']=np.sin(PC['alfa_f'])+np.cos(PC['alfa_f'])
PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
PC['fs']=PC['fst Ast']/PC['bw']/PC['he']

X = PC[['fc', 'Ls/he', 'fs', 'Sst/he', 'Sf/he','fr', 'si_co']];     PC['vs'] = PC['V']/PC['bw']/PC['he']*1000.0


PC['L_d']=PC['Ls/he'];PC['sst']=PC['Sst/he'];PC['sf']=PC['Sf/he'];PC['fs']=np.maximum(0.001,PC['fs']);PC['fr']=np.maximum(0.001,PC['fr'])

features = ['fc','L_d', 'sst', 'sf', 'si_co', 'fs','fr']
X=PC[features];y=PC['vs']

modelior11=[]
for j in range(50):
    #population_size is the equation size
    model7 = PySRRegressor(niterations=100,populations=40,population_size=35,maxsize=35,
                      nested_constraints={"^":{"^":0}},parsimony= 0.00,#adaptive_parsimony_scaling=1000,
                      constraints={"^":(-1,10)},
                      binary_operators=["*","^"],#elementwise_loss="f(y, x) = ((x+0.00001)/(y+0.00001)-1.0)^2",#special(x,y)=x^2.0+y
                      model_selection ='accuracy',loss_function=objective,should_simplify=False,use_frequency=False
                      )
    model7.fit(X,y)
    i=0
    modelior11.append(model7)
    while i <len(model7.equations_):
        print(model7.sympy(i))
        i=i+1

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 7.580e+04
Head worker occupation: 11.8%
Progress: 150 / 4000 total iterations (3.750%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fc
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.108e-02  y = (L_d ^ ((si_co * sf) * fs))
9           4.004e+02  1.113e-01  y = (L_d * (fr * (sst * (fc ^ fs))))
11          3.006e+02  1.434e-01  y = (L_d * ((sf ^ fc) * ((fs * fc) * sst)))
13          2.008e+02  2.017e-01  y = (L_d * (((si_co * sf) * fc) * ((fs ^ fc) * sst)))
15          1.007e+02  3.451e-01  y = (L_d * ((((fc * fr) ^ sf) * si_co) * (sst ^ (fc * fs))))
17          9.605e-01  2.326e+00  y = ((fc * L_d) * ((fr * (sf ^ (si_co * fc))) * ((sst * fc) ^ ...
                                  fs)))
19          5.931e-01  2.411e-01  y = ((fc ^ (L_d * -0.56766)) * ((((fc * si_co) * f

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 2.920e+04
Head worker occupation: 5.6%
Progress: 69 / 4000 total iterations (1.725%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.38727
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.108e-02  y = (L_d ^ ((si_co * sf) * fs))
9           4.003e+02  1.114e-01  y = (L_d * ((si_co * fr) * (fs ^ sst)))
11          3.008e+02  1.428e-01  y = (L_d ^ ((sf * (fc * si_co)) * (sst * fs)))
13          2.005e+02  2.029e-01  y = (L_d * ((fr * (sf ^ (fc * si_co))) * (fs * sst)))
15          1.009e+02  3.433e-01  y = (L_d * ((fr * (sf * (fc * si_co))) * (fc ^ (fs * sst))))
17          9.991e-01  2.307e+00  y = ((fc ^ L_d) * (((si_co * (fr * sf)) ^ fc) * (fs ^ (sst * f...
                                  c))))
19          8.945e-01  5.529e-02  y = (((L_d ^ -0.47572) * fc) * (((sf ^ fr

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!


...


Expressions evaluated per second: 8.140e+04
Head worker occupation: 10.3%
Progress: 163 / 4000 total iterations (4.075%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = -0.76446
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.108e-02  y = (L_d * ((si_co * sf) ^ fs))
9           4.003e+02  1.115e-01  y = (L_d ^ (((si_co * sf) * fr) * fs))
11          3.009e+02  1.427e-01  y = (L_d ^ (((si_co * (sf * fc)) * fr) * fs))
13          2.009e+02  2.019e-01  y = (L_d * (((sf * si_co) * (fc * fr)) ^ (sst * fc)))
15          1.008e+02  3.452e-01  y = (L_d * ((fc * (sf ^ (si_co * fr))) * ((fc * sst) * fs)))
17          9.636e-01  2.325e+00  y = ((L_d * fc) * ((fc * (sf ^ (si_co * fr))) * ((fc * sst) ^ ...
                                  fs)))
19          3.396e-01  5.214e-01  y = (((L_d * fc) ^ 0.29408) * ((fr * ((s

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 6.890e+04
Head worker occupation: 7.5%
Progress: 137 / 4000 total iterations (3.425%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.38727
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.110e-02  y = (L_d * ((si_co * sf) ^ sst))
9           4.008e+02  1.108e-01  y = (L_d * (((si_co * fc) * sf) ^ sst))
11          3.007e+02  1.438e-01  y = (L_d ^ (((si_co * fr) * sf) * (fs * fc)))
13          2.009e+02  2.015e-01  y = (fc * ((si_co * (sf ^ (fr * fc))) * (fc * sst)))
15          1.006e+02  3.458e-01  y = (L_d * ((((si_co * fr) * sf) ^ fc) * ((fc * sst) ^ fs)))
17          9.593e-01  2.327e+00  y = ((L_d * fc) * ((((sf ^ fc) * si_co) * fr) * ((fs ^ fc) * s...
                                  st)))
19          2.479e-01  6.766e-01  y = (((L_d * fc) ^ 0.30186) * (((sf ^ (fr

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 7.550e+04
Head worker occupation: 13.0%
Progress: 152 / 4000 total iterations (3.800%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 1.4146
5           6.002e+02  7.033e-01  y = (L_d ^ (si_co * fs))
7           5.003e+02  9.109e-02  y = (L_d * ((sf ^ fr) * sst))
9           4.006e+02  1.111e-01  y = (L_d * (sf ^ ((sst * fc) * fs)))
11          3.009e+02  1.430e-01  y = (L_d * (((si_co * fr) * fc) ^ (sst * fs)))
13          2.009e+02  2.020e-01  y = (L_d * ((fc * ((fr * sf) * si_co)) ^ (fc * fs)))
15          1.008e+02  3.449e-01  y = (L_d * ((fc * ((si_co * sf) ^ fr)) * (fs * (fc * sst))))
17          9.648e-01  2.325e+00  y = ((L_d * fc) * ((((fc * fr) * si_co) ^ sf) * ((fs * sst) ^ ...
                                  fc)))
19          3.127e-01  5.634e-01  y = ((L_d * (fc ^ 0.090378)) * (((sf ^ fc) * (

In [ ]:
#PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
#binary_operators=["*","^"]
objective = """
function my_custom_objective(tree, dataset::Dataset{T,L}, options) where {T,L} 
    penalty_term = L(0)
    tot_features = 1:7
    tol = L(0.0000000000000001)
    
    P_pred = dataset.X[1,:]
    
    if tree.degree != 2
        penalty_term += L(10000)
    else
        fn = tree.l
        vfc, flag = eval_tree_array(fn, dataset.X, options)
        if !flag
            return L(Inf)
        end
        penalty_term += any(x -> x < 0, vfc) ? L(100) : L(0)
            
        if  tree.r.degree != 2  
            penalty_term += L(10000)
        else
            fn = tree.r.r
            vs, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vs) ? L(100) : L(0)

            fn = tree.r.l
            vf, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vf) ? L(100) : L(0)
            P_pred = (vfc .+  vs .+  vf) 
        end
    end
    dims = size(dataset.y)
    #println("y: ", dims)
    dims = size(P_pred)
    #println("P_pred: ", dims)
    r = dataset.y ./P_pred .- 1.0
    MAPE = sum(abs.(r)) ./ length(r)
    return ( penalty_term  + MAPE )
end

my_custom_objective
"""
from pysr import PySRRegressor
import numpy as np
import scipy.io as sio
import pandas as pd
#aaaaaaaaaaaa
data = pd.read_excel('data111.xlsx', sheet_name='1_17')
PC = data[data['ff'] != 0][['fc', 'he', 'hf', 'bw', 'bf', 'Ls/he', 'fst Ast', 'Sst/he', 'Al', 'ff', 'EfAf', 'Sf/he', 'Rg', 'alfa_f', 'V']].copy();PC['Vexp']=PC['V']
PC['alfa_f'] = PC['alfa_f'] * (np.pi / 180)
PC['si_co']=np.sin(PC['alfa_f'])+np.cos(PC['alfa_f'])
PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
PC['fs']=PC['fst Ast']/PC['bw']/PC['he']

X = PC[['fc', 'Ls/he', 'fs', 'Sst/he', 'Sf/he','fr', 'si_co']];     PC['vs'] = PC['V']/PC['bw']/PC['he']*1000.0


PC['L_d']=PC['Ls/he'];PC['sst']=PC['Sst/he'];PC['sf']=PC['Sf/he'];PC['fs']=np.maximum(0.001,PC['fs']);PC['fr']=np.maximum(0.001,PC['fr'])

features = ['fc','L_d', 'sst', 'sf', 'si_co', 'fs','fr']
X=PC[features];y=PC['vs']

modelior11=[]
for j in range(20):
    #population_size is the equation size
    model7 = PySRRegressor(niterations=100,populations=40,population_size=35,maxsize=35,
                      nested_constraints={"^":{"^":1}},parsimony= 0.01,#adaptive_parsimony_scaling=1000,
                      constraints={"^":(-1,10)},
                      binary_operators=["*","^"],#elementwise_loss="f(y, x) = ((x+0.00001)/(y+0.00001)-1.0)^2",#special(x,y)=x^2.0+y
                      model_selection ='accuracy',loss_function=objective,
                      )
    model7.fit(X,y)
    i=0
    modelior11.append(model7)
    while i <len(model7.equations_):
        print(model7.sympy(i))
        i=i+1

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.290e+05
Head worker occupation: 14.2%
Progress: 284 / 4000 total iterations (7.100%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.75466
5           1.960e-01  2.709e+00  y = (1.5127 ^ (fs * 2.0787))
7           1.718e-01  6.575e-02  y = ((fc ^ 0.32381) ^ (fs * fs))
9           1.633e-01  2.539e-02  y = ((fc ^ 0.32381) ^ ((fs ^ sst) * fs))
11          1.554e-01  2.493e-02  y = ((fc ^ 0.32381) * ((fs ^ (sst ^ fr)) * fs))
---------------------------------------------------------------------------------------------------
Press 'q' and then <enter> to stop execution early.

Expressions evaluated per second: 1.460e+05
Head worker occupation: 18.9%
Progress: 612 / 4000 total iterations (15.300%)
Hall of Fame:
---------------------------------------------------------------------------------------------------


c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.390e+05
Head worker occupation: 12.6%
Progress: 305 / 4000 total iterations (7.625%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fs
5           1.919e-01  2.714e+00  y = (3.3173 * (fs * fs))
7           1.772e-01  3.993e-02  y = ((fc ^ 0.29083) * (fs ^ 0.7786))
9           1.717e-01  1.567e-02  y = ((fc ^ 0.29083) * ((fs ^ sf) ^ 0.50813))
11          1.650e-01  1.994e-02  y = ((fc ^ 0.29083) * ((fs ^ (sf * sf)) ^ fs))
23          1.638e-01  5.975e-04  y = (((fc ^ (1.0674 * 0.44845)) * (((0.38153 * 0.8526) * 0.381...
                                  53) ^ 0.32348)) * ((((0.53203 * fr) * fs) ^ 0.5227) * 0.49666)...
                                  )
25          1.594e-01  1.373e-02  y = (((fc ^ (1.082 * 0.34611)) * ((si_co * 0.34611) ^ 0.34611)...
                                  ) * (((((0.46174 * fr

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!


...


Expressions evaluated per second: 1.670e+05
Head worker occupation: 15.0%
Progress: 343 / 4000 total iterations (8.575%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.51937
5           1.919e-01  2.714e+00  y = (fs * (fs * 3.3229))
7           1.753e-01  4.528e-02  y = ((fc ^ 0.31907) * (fs * fs))
9           1.750e-01  1.001e-03  y = (fs ^ ((0.57923 * 0.72852) * (fc ^ 0.31482)))
11          1.731e-01  5.484e-03  y = ((fs ^ 0.41265) ^ ((0.57923 * fs) * (fc ^ 0.31482)))
13          1.694e-01  1.058e-02  y = ((fs ^ (sf * sf)) * (0.5611 * ((fc * 0.5611) ^ 0.31482)))
15          1.662e-01  9.471e-03  y = ((fs ^ (sf * sf)) * ((0.57923 ^ sst) * ((fc * 0.5611) ^ 0....
                                  31482)))
17          1.634e-01  8.705e-03  y = ((fs ^ (sf ^ 0.73777)) * (((0.55059 ^ sf) ^ sst) * ((fc * ...
                                  0.

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.640e+05
Head worker occupation: 18.3%
Progress: 352 / 4000 total iterations (8.800%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 1.9017
5           1.919e-01  2.714e+00  y = (3.3201 ^ (fs ^ fs))
7           1.755e-01  4.476e-02  y = (0.036126 * ((fc ^ 0.34752) * fs))
9           1.748e-01  2.064e-03  y = ((0.90726 ^ fc) * ((fc ^ 0.34752) * fs))
11          1.704e-01  1.278e-02  y = (((fc ^ -0.91965) ^ sst) * ((fc ^ 0.34752) * fs))
13          1.628e-01  2.276e-02  y = (((fc ^ -0.91965) ^ (sst ^ fr)) * ((fc ^ 0.34752) * fs))
33          1.614e-01  4.247e-04  y = (((1.388 ^ (L_d * fs)) * (si_co ^ si_co)) * (((0.69041 ^ s...
                                  f) * ((((((si_co * (L_d * L_d)) * 0.69041) * (1.388 ^ sst)) * ...
                                  si_co) * 0.11131) ^ -1.0046)) * si_co))
35       

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.560e+05
Head worker occupation: 19.4%
Progress: 323 / 4000 total iterations (8.075%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.38727
5           1.960e-01  2.708e+00  y = (fs * (1.7982 ^ 1.7982))
7           1.838e-01  3.224e-02  y = ((fc ^ 0.32234) ^ (0.3358 ^ 0.32234))
9           1.806e-01  8.725e-03  y = ((fc ^ (0.87055 * 0.32234)) * (0.67037 ^ fs))
11          1.789e-01  4.583e-03  y = ((fc ^ (0.87055 * 0.32234)) * ((0.67037 * si_co) ^ fs))
17          1.760e-01  2.732e-03  y = ((0.59422 ^ -0.13095) * (L_d * ((fc ^ (0.46119 ^ si_co)) *...
                                   (0.64962 ^ (L_d ^ L_d)))))
19          1.698e-01  1.803e-02  y = (((0.14275 * fc) ^ 0.68808) * ((0.026411 * L_d) * (fs ^ ((...
                                  fs * L_d) * (sst ^ fr)))))
25          1.667e-01  3.091e-03  y 

In [8]:
#PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
#binary_operators=["*","^"]
objective = """
function my_custom_objective(tree, dataset::Dataset{T,L}, options) where {T,L} 
    penalty_term = L(0)
    tot_features = 1:7
    tol = L(0.0000000000000001)
    
    P_pred = dataset.X[1,:]
    
    if tree.degree != 2
        penalty_term += L(10000)
    else
        fn = tree.l
        vfc, flag = eval_tree_array(fn, dataset.X, options)
        if !flag
            return L(Inf)
        end
        penalty_term += any(x -> x < 0, vfc) ? L(100) : L(0)
            
        if  tree.r.degree != 2  
            penalty_term += L(10000)
        else
            fn = tree.r.r
            vs, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vs) ? L(100) : L(0)

            fn = tree.r.l
            vf, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vf) ? L(100) : L(0)
            P_pred = (vfc .+  vs .+  vf) 
        end
    end
    dims = size(dataset.y)
    #println("y: ", dims)
    dims = size(P_pred)
    #println("P_pred: ", dims)
    r = dataset.y ./P_pred .- 1.0
    MAPE = sum(abs.(r)) ./ length(r)
    return ( penalty_term  + MAPE )
end

my_custom_objective
"""
from pysr import PySRRegressor
import numpy as np
import scipy.io as sio
import pandas as pd
#aaaaaaaaaaaa
data = pd.read_excel('data111.xlsx', sheet_name='1_17')
PC = data[data['ff'] != 0][['fc', 'he', 'hf', 'bw', 'bf', 'Ls/he', 'fst Ast', 'Sst/he', 'Al', 'ff', 'EfAf', 'Sf/he', 'Rg', 'alfa_f', 'V']].copy();PC['Vexp']=PC['V']
PC['alfa_f'] = PC['alfa_f'] * (np.pi / 180)
PC['si_co']=np.sin(PC['alfa_f'])+np.cos(PC['alfa_f'])
PC['fr']=PC['EfAf']/PC['bw']/PC['he']/PC['fc']
PC['fs']=PC['fst Ast']/PC['bw']/PC['he']

X = PC[['fc', 'Ls/he', 'fs', 'Sst/he', 'Sf/he','fr', 'si_co']];     PC['vs'] = PC['V']/PC['bw']/PC['he']*1000.0


PC['L_d']=PC['Ls/he'];PC['sst']=PC['Sst/he'];PC['sf']=PC['Sf/he'];PC['fs']=np.maximum(0.001,PC['fs']);PC['fr']=np.maximum(0.001,PC['fr'])

features = ['fc','L_d', 'sst', 'sf', 'si_co', 'fs','fr']
X=PC[features];y=PC['vs']

modelior11=[]
for j in range(20):
    #population_size is the equation size
    model7 = PySRRegressor(niterations=100,populations=40,population_size=35,maxsize=35,
                      nested_constraints={"^":{"^":1}},parsimony= 0.01,#adaptive_parsimony_scaling=1000,
                      constraints={"^":(-1,10)},
                      binary_operators=["*","^"],#elementwise_loss="f(y, x) = ((x+0.00001)/(y+0.00001)-1.0)^2",#special(x,y)=x^2.0+y
                      model_selection ='accuracy',loss_function=objective,
                      )
    model7.fit(X,y)
    i=0
    modelior11.append(model7)
    while i <len(model7.equations_):
        print(model7.sympy(i))
        i=i+1

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 9.820e+04
Head worker occupation: 12.7%
Progress: 222 / 4000 total iterations (5.550%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fs
5           1.919e-01  2.714e+00  y = (3.3229 ^ (fs ^ fs))
7           1.706e-01  5.891e-02  y = (fs * (fs * (fc ^ 0.34333)))
11          1.682e-01  3.585e-03  y = ((fs ^ (1.2734 ^ sst)) * (fs * (fc ^ 0.34333)))
13          1.641e-01  1.238e-02  y = (((fs ^ L_d) * (fc ^ 0.34333)) * (fs ^ (fc ^ 0.34333)))
15          1.625e-01  4.907e-03  y = (((fs ^ 1.4955) ^ (sst ^ si_co)) * ((fs * fs) * (fc ^ 0.34...
                                  333)))
17          1.586e-01  1.214e-02  y = (((fs ^ 1.4955) ^ (sst ^ si_co)) * (((fs * L_d) * fs) * (f...
                                  c ^ 0.34333)))
-------------------------------------------------------------------------------------

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.440e+05
Head worker occupation: 15.2%
Progress: 308 / 4000 total iterations (7.700%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.75466
5           1.919e-01  2.714e+00  y = (fs * (3.3209 * fs))
7           1.797e-01  3.298e-02  y = (fs ^ (0.90533 * (fc ^ 0.283)))
9           1.766e-01  8.493e-03  y = (0.283 ^ (fs * ((fc * 1.9915) ^ 0.283)))
11          1.702e-01  1.850e-02  y = (0.283 ^ ((fs ^ sf) * ((fc * si_co) ^ 0.283)))
15          1.692e-01  1.498e-03  y = ((0.283 ^ ((sf * 1.2886) * sf)) ^ ((0.283 ^ sst) * (fc ^ 0...
                                  .283)))
17          1.664e-01  8.500e-03  y = (((1.7399 ^ 1.851) * (fs * (1.3199 ^ -0.27858))) ^ (0.1210...
                                  6 * ((fc * 0.68589) ^ 0.3471)))
29          1.586e-01  3.968e-03  y = (((-1.183 * (1.3333 * (((si_co * 0.85

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!


...

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.650e+05
Head worker occupation: 19.0%
Progress: 356 / 4000 total iterations (8.900%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fs
5           1.960e-01  2.709e+00  y = (2.2667 * (1.3247 * fs))
7           1.711e-01  6.786e-02  y = ((fc ^ 0.3248) * (fs * fs))
9           1.634e-01  2.294e-02  y = ((fc ^ 0.3248) * ((fs ^ sst) * fs))
11          1.604e-01  9.267e-03  y = ((fc ^ 0.30275) ^ ((fs ^ sf) * (fs ^ sst)))
29          1.590e-01  5.057e-04  y = (fs * ((((0.31456 ^ sf) * (fc * fc)) ^ (0.31048 * 0.57896)...
                                  ) * (fs * ((((0.31456 ^ 0.64088) * (fc * fc)) ^ (0.31048 * 0.5...
                                  7896)) * fs))))
31          1.557e-01  1.056e-02  y = ((si_co ^ -0.28554) * ((((0.31456 ^ 0.64088) * (fc * fc)) ...
                                  ^ ((0.31456 

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.580e+05
Head worker occupation: 18.6%
Progress: 340 / 4000 total iterations (8.500%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.059071
5           1.919e-01  2.714e+00  y = (fs ^ (3.3229 ^ fs))
7           1.874e-01  1.192e-02  y = ((1.0155 ^ fc) * (1.0155 * 1.0155))
9           1.722e-01  4.243e-02  y = ((0.039077 * fc) * ((fs * L_d) * 1.744))
11          1.676e-01  1.356e-02  y = ((0.06219 * fc) * (((0.41999 ^ sst) * fr) ^ 0.69802))
13          1.660e-01  4.681e-03  y = (((fr ^ 0.32) * fs) * ((0.32 * (fc ^ 0.52045)) ^ 1.379))
15          1.645e-01  4.454e-03  y = (((fr * (fr ^ -0.61869)) * fs) * ((0.32 * (fc ^ 0.52045)) ...
                                  ^ 1.379))
17          1.605e-01  1.252e-02  y = (((fc * (0.31193 ^ sf)) ^ 0.31193) * (((fr * fs) * 0.31193...
                                

FileNotFoundError: [WinError 3] The system cannot find the path specified: 'C:\\Users\\osama\\AppData\\Local\\Temp\\tmph90rp3n7'

In [3]:
objective = """
function my_custom_objective(tree, dataset::Dataset{T,L}, options) where {T,L} 
    penalty_term = L(0)
    tot_features = 1:7
    tol = L(0.0000000000000001)
    
    P_pred = dataset.X[1,:]
    
    if tree.degree != 2
        penalty_term += L(10000)
    else
        fn = tree.l
        vfc, flag = eval_tree_array(fn, dataset.X, options)
        if !flag
            return L(Inf)
        end
        penalty_term += any(x -> x < 0, vfc) ? L(100) : L(0)
            
        if  tree.r.degree != 2  
            penalty_term += L(10000)
        else
            fn = tree.r.r
            vs, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vs) ? L(100) : L(0)

            fn = tree.r.l
            vf, flag = eval_tree_array(fn, dataset.X, options)
            if !flag
                return L(Inf)
            end
            penalty_term += any(x -> x < 0, vf) ? L(100) : L(0)
            P_pred = (vfc .+  vs .+  vf) 
        end
    end
    dims = size(dataset.y)
    #println("y: ", dims)
    dims = size(P_pred)
    #println("P_pred: ", dims)
    r = dataset.y ./P_pred .- 1.0
    MAPE = sum(abs.(r)) ./ length(r)
    return ( penalty_term  + MAPE )
end

my_custom_objective
"""
from pysr import PySRRegressor
import numpy as np
import scipy.io as sio
import pandas as pd
#aaaaaaaaaaaa
data = pd.read_excel('data111.xlsx', sheet_name='1_17')
PC = data[data['ff'] != 0][['fc', 'he', 'hf', 'bw', 'bf', 'Ls/he', 'fst Ast', 'Sst/he', 'Al', 'ff', 'EfAf', 'Sf/he', 'Rg', 'alfa_f', 'V']].copy();PC['Vexp']=PC['V']
PC['alfa_f'] = PC['alfa_f'] * (np.pi / 180)
PC['si_co']=np.sin(PC['alfa_f'])+np.cos(PC['alfa_f'])
PC['fr']=PC['EfAf']/PC['bw']/PC['he']
PC['fs']=PC['fst Ast']/PC['bw']/PC['he']

X = PC[['fc', 'Ls/he', 'fs', 'Sst/he', 'Sf/he','fr', 'si_co']];     PC['vs'] = PC['V']/PC['bw']/PC['he']*1000.0


PC['L_d']=PC['Ls/he'];PC['sst']=PC['Sst/he'];PC['sf']=PC['Sf/he'];PC['fs']=np.maximum(0.001,PC['fs']);PC['fr']=np.maximum(0.001,PC['fr'])

features = ['fc','L_d', 'sst', 'sf', 'si_co', 'fs','fr']
X=PC[features];y=PC['vs']

modelior11=[]
for j in range(100):
    #population_size is the equation size
    model7 = PySRRegressor(niterations=100,populations=40,population_size=35,maxsize=35,
                      nested_constraints={"^":{"^":1}},parsimony= 0.01,#adaptive_parsimony_scaling=1000,
                      constraints={"^":(-1,10)},
                      binary_operators=["+", "*","^"],#elementwise_loss="f(y, x) = ((x+0.00001)/(y+0.00001)-1.0)^2",#special(x,y)=x^2.0+y
                      model_selection ='accuracy',loss_function=objective,
                      )
    model7.fit(X,y)
    i=0
    modelior11.append(model7)
    while i <len(model7.equations_):
        print(model7.sympy(i))
        i=i+1

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.330e+05
Head worker occupation: 12.6%
Progress: 275 / 4000 total iterations (6.875%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.33265
5           1.960e-01  2.709e+00  y = (fs + (3.1169 * 0.47449))
7           1.896e-01  1.671e-02  y = (fs + (3.1169 + (0.40567 ^ sst)))
9           1.888e-01  2.058e-03  y = (((fs ^ sst) * si_co) + (0.33046 + 3.1169))
11          1.866e-01  5.875e-03  y = (((fs ^ sst) * (L_d + -1.242)) + (0.33046 + 3.1169))
13          1.787e-01  2.142e-02  y = ((fs + ((fc * 0.14333) * 0.14333)) * (1.6476 + (1.2452 ^ 0...
                                  .39637)))
15          1.709e-01  2.241e-02  y = ((fs + ((0.49194 * 0.071065) * fc)) * ((0.24513 ^ sf) + (1...
                                  .2452 + 0.39637)))
17          1.707e-01  7.032e-04  y = (0.59764 + (((0.41969 ^ sf) + ((

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.380e+05
Head worker occupation: 21.7%. This is high, and will prevent efficient resource usage. Increase `ncyclesperiteration` to reduce load on head worker.
Progress: 296 / 4000 total iterations (7.400%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.7282
5           1.960e-01  2.709e+00  y = (fs * (1.4491 * 2.1423))
7           1.685e-01  7.549e-02  y = (fs + ((fc ^ 0.33385) ^ fs))
9           1.643e-01  1.275e-02  y = ((fc ^ 0.31558) + ((fs ^ sf) * fs))
11          1.637e-01  1.842e-03  y = (((fc + fs) ^ 0.31558) + ((fs ^ sst) ^ fs))
33          1.571e-01  1.877e-03  y = ((((-1.5897 * si_co) * -0.23811) + 0.52826) + (((((0.52826...
                                   + fs) ^ L_d) * fr) * (((L_d + si_co) * 0.021486) ^ (0.56721 +...
                                   (0.56721 * L_d)))) * ((0.52826 * fc)

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!


...


Expressions evaluated per second: 1.390e+05
Head worker occupation: 17.5%
Progress: 291 / 4000 total iterations (7.275%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 0.11641
5           1.960e-01  2.708e+00  y = (fs ^ (2.2426 * 1.3524))
7           1.687e-01  7.501e-02  y = (fs + (fs + (fc ^ 0.33629)))
15          1.669e-01  1.360e-03  y = ((((0.1166 + fc) * 0.18399) ^ 0.46638) * ((-0.15408 + (L_d...
                                   ^ fs)) ^ fs))
27          1.619e-01  2.531e-03  y = ((((1.4228 ^ -0.024386) + fs) + (((0.1166 * fc) + (((sf + ...
                                  0.056314) * sst) * -0.7948)) ^ 0.46638)) * ((-0.64352 + (L_d ^...
                                   fs)) + 0.1357))
31          1.599e-01  3.055e-03  y = ((((1.4228 ^ -0.024386) + fs) + (((0.1166 * fc) + (((sf + ...
                                  0.056314) * 

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.350e+05
Head worker occupation: 16.6%
Progress: 286 / 4000 total iterations (7.150%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = 1.3717
5           1.919e-01  2.714e+00  y = (3.3229 + (fs + fs))
7           1.888e-01  8.151e-03  y = ((fc ^ 0.25201) + (0.3834 + 0.90228))
9           1.767e-01  3.322e-02  y = (((fc ^ 0.34261) + -0.51996) ^ (0.55193 ^ fs))
11          1.707e-01  1.727e-02  y = ((fc ^ (0.25201 ^ 0.89557)) + ((0.44255 + fs) + fs))
13          1.695e-01  3.588e-03  y = ((((0.67423 * (fs + fc)) ^ 0.35952) + fs) + (fs + fs))
17          1.669e-01  3.847e-03  y = (((fc ^ 0.25201) + fs) + ((L_d ^ (-0.35415 * (sst + sf))) ...
                                  + (0.26981 + fs)))
25          1.653e-01  1.161e-03  y = ((((0.67423 * ((((-1.6077 * (sst + sf)) + 1.7691) + ((sst ...
                    

c:\Users\osama\anaconda3\lib\site-packages\pysr\sr.py:1297: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
[ Info: Started!



Expressions evaluated per second: 1.410e+05
Head worker occupation: 17.1%
Progress: 297 / 4000 total iterations (7.425%)
Hall of Fame:
---------------------------------------------------------------------------------------------------
Complexity  Loss       Score     Equation
1           1.000e+04  1.594e+01  y = fc
5           1.919e-01  2.714e+00  y = (fs * (3.3175 + fs))
7           1.747e-01  4.714e-02  y = (fs * (0.28853 * (fc ^ 0.32942)))
9           1.695e-01  1.483e-02  y = (fs ^ (fs + ((fc * 0.51272) ^ 0.40621)))
11          1.643e-01  1.564e-02  y = ((fs ^ sst) ^ (fs + ((fc * 0.51272) ^ 0.40621)))
---------------------------------------------------------------------------------------------------
Press 'q' and then <enter> to stop execution early.

Expressions evaluated per second: 1.480e+05
Head worker occupation: 15.5%
Progress: 625 / 4000 total iterations (15.625%)
Hall of Fame:
-----------------------------------------------------------------------------------------------